# Visualize RiOMAR dggs-transformed data with xddgs and lonboard

## Context

### Purpose

The goal is to visualize the DGGS transformed RiOMar data with xdggs and lonboard. 

### Description

In this notebook, we will:
- Open DGGS RiOMar dataset
- Visualize it using a colorblind-friendly colormap 

## Contributions

### Notebook

- Anne Fouilloux, Simula Research Laboratory (Norway), @annefou

## Bibliography and other interesting resources
- [xdggs](http://xdggs.readthedocs.io/en/latest/)
- [lonboard](https://developmentseed.org/lonboard/latest/)

## Install Libraries
- We need to use a newer version of xdggs

In [ ]:
pip install git+https://github.com/xarray-contrib/xdggs cmcrameri

In [1]:
import xdggs
import xarray as xr
from cmcrameri import cm

## Open file with xdggs

In [2]:
nside = 4096
dout = xr.open_zarr("https://data-fair2adapt.ifremer.fr/riomar/small_healpix.zarr")
dout = (
    dout.load()
    .drop_vars(["latitude", "longitude"])
    .stack(cell=["x", "y"], create_index=False)
)
dout

<xarray.Dataset> Size: 391MB
Dimensions:       (cells: 242076, s_rho: 40, time_counter: 5)
Coordinates:
    cell_ids      (cells) uint64 2MB 11190229 11190230 ... 57954657 57954658
    resolution    float64 8B 0.0002498
  * s_rho         (s_rho) float32 160B -0.9875 -0.9625 ... -0.0375 -0.0125
  * time_counter  (time_counter) datetime64[ns] 40B 2004-01-01T00:58:30 ... 2...
    time_instant  (time_counter) datetime64[ns] 40B 2004-01-01T00:58:30 ... 2...
Dimensions without coordinates: cells
Data variables:
    ocean_mask    (cells) float64 2MB nan nan nan nan nan ... 1.0 1.0 1.0 1.0
    temp          (time_counter, s_rho, cells) float64 387MB nan nan ... 10.47
Attributes:
    grid_type:  healpix
    lat:        0
    level:      12
    lon:        0
    nside:      4096
    rot_lat:    0
    rot_lon:    0

In [3]:
dout_idx = dout.dggs.decode(
    {
        "grid_name": "healpix",
        "nside": nside,
        "nest": True,
    }
)
cell_centers = dout_idx.dggs.cell_centers()
dout_idx = dout_idx.assign_coords(
    cell_centers.coords
)
dout_idx

<xarray.Dataset> Size: 395MB
Dimensions:       (cells: 242076, s_rho: 40, time_counter: 5)
Coordinates:
  * cell_ids      (cells) uint64 2MB 11190229 11190230 ... 57954657 57954658
    resolution    float64 8B 0.0002498
  * s_rho         (s_rho) float32 160B -0.9875 -0.9625 ... -0.0375 -0.0125
  * time_counter  (time_counter) datetime64[ns] 40B 2004-01-01T00:58:30 ... 2...
    time_instant  (time_counter) datetime64[ns] 40B 2004-01-01T00:58:30 ... 2...
    latitude      (cells) float64 2MB 43.31 43.31 43.32 ... 50.83 50.84 50.84
    longitude     (cells) float64 2MB 0.1698 0.1471 0.1472 ... 352.1 352.1 352.1
Dimensions without coordinates: cells
Data variables:
    ocean_mask    (cells) float64 2MB nan nan nan nan nan ... 1.0 1.0 1.0 1.0
    temp          (time_counter, s_rho, cells) float64 387MB nan nan ... 10.47
Indexes:
    cell_ids  HealpixIndex(level=12, indexing_scheme=nested)
Attributes:
    grid_type:  healpix
    lat:        0
    level:      12
    lon:        0
    nside:      4096
    rot_lat:    0
    rot_lon:    0

In [4]:
display(dout_idx.temp.min(), dout_idx.temp.max())

<xarray.DataArray 'temp' ()> Size: 8B
array(2.00370111)
Coordinates:
    resolution  float64 8B 0.0002498

<xarray.DataArray 'temp' ()> Size: 8B
array(13.97993374)
Coordinates:
    resolution  float64 8B 0.0002498

In [ ]:
dout_idx.temp.isel(time_counter=0, s_rho=0).dggs.explore(center=7, cmap=cm.oleron, alpha=0.8)